In [9]:
import scipy.optimize
import numpy as np

import time

import cirq
import openfermion
from openfermion.ops import FermionOperator
from openfermion import gaussian_state_preparation_circuit

from qiskit.extensions import UnitaryGate

from qiskit import QuantumRegister, QuantumCircuit

from itertools import combinations

from qiskit import QuantumCircuit, transpile, Aer, IBMQ
from qiskit.tools.jupyter import *
from qiskit.visualization import *

# Loading your IBM Quantum account(s)

from qiskit.quantum_info.operators import Operator

#define the custom RYXXY gate

def YXXY(fi):
    arr = np.array([[ 1.0,  0.0,  0.0,  0.0],
       [ 0.0, np.cos(fi),  np.sin(fi),  0.0], #ne ovde- some radom comments in Serbian
       [ 0.0, -np.sin(fi),  np.cos(fi),  0.0], #minus ovde
       [ 0.0,  0.0,  0.0,   1.0]])
    u_gate = UnitaryGate(data = arr,label = 'RYXXY('+str(fi)+")")
    return u_gate



def gauss_state_qiskit(circ_aux, OccupOrb, nqbit,mu):
    hubbard_model = FermionOperator(circ_aux[0:len(circ_aux)-1])
    #print("HM",hubbard_model)
    quad_ham = openfermion.get_quadratic_hamiltonian(hubbard_model,ignore_incompatible_terms=True)
    circuit_description, start_orbitals = gaussian_state_preparation_circuit(quad_ham, occupied_orbitals=OccupOrb, spin_sector=None)
    nr_var_par=0
#    print("CD",circuit_description)
#    print("CA",circ_aux)
#    print("QH",quad_ham)
    var_ar=[]
    qr = QuantumRegister(nqbit, 'q')
    qc = QuantumCircuit(qr)
    #go through the cirq circuitand give a qiskit one
    for i in start_orbitals:
        qc.x(qr[i])
    for i in range(0,len(circuit_description)):
        for j in range (0,len(circuit_description[i])):
            if type(circuit_description[i][j])==tuple:
                qc.unitary(YXXY(circuit_description[i][j][2]), [qr[int(circuit_description[i][j][0])], qr[int(circuit_description[i][j][1])]])
                qc.rz(circuit_description[i][j][3],qr[int(circuit_description[i][j][1])])
                nr_var_par+=2
                var_ar.append(circuit_description[i][j][2])
                var_ar.append(circuit_description[i][j][3])
            else:
                qc.x(qr[nqbit-1])

    return qc,OccupOrb,nqbit,mu